# Imports

In [ ]:
%pip install google-colab-selenium

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.4/9.4 MB 51.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 476.0/476.0 kB 25.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 4.2 MB/s eta 0:00:00


In [ ]:
# Set up for running selenium in Google Colab
## You don't need to run this code if you do it in Jupyter notebook, or other local Python setting
%%shell
sudo apt -y update
sudo apt install -y wget curl unzip
wget http://archive.ubuntu.com/ubuntu/pool/main/libu/libu2f-host/libu2f-udev_1.1.4-1_all.deb
dpkg -i libu2f-udev_1.1.4-1_all.deb
wget https://dl.google.com/linux/direct/google-chrome-stable_current_amd64.deb
dpkg -i google-chrome-stable_current_amd64.deb
CHROME_DRIVER_VERSION=`curl -sS chromedriver.storage.googleapis.com/LATEST_RELEASE`
wget -N https://chromedriver.storage.googleapis.com/$CHROME_DRIVER_VERSION/chromedriver_linux64.zip -P /tmp/
unzip -o /tmp/chromedriver_linux64.zip -d /tmp/
chmod +x /tmp/chromedriver
mv /tmp/chromedriver /usr/local/bin/chromedriver
pip install selenium

Get:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,626 B]
Hit:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Hit:3 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:4 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Get:5 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [128 kB]
Ign:6 https://r2u.stat.illinois.edu/ubuntu jammy InRelease
Get:7 https://r2u.stat.illinois.edu/ubuntu jammy Release [5,713 B]
Get:8 https://r2u.stat.illinois.edu/ubuntu jammy Release.gpg [793 B]
Get:9 http://archive.ubuntu.com/ubuntu jammy-backports InRelease [127 kB]
Get:10 http://security.ubuntu.com/ubuntu jammy-security/main amd64 Packages [2,169 kB]
Get:11 https://r2u.stat.illinois.edu/ubuntu jammy/main amd64 Packages [2,553 kB]
Hit:12 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Get:13 http://archive.ubuntu.com/ubuntu jammy-updates/universe amd64 Packages [1,422 kB]
Hit:14 https://ppa

In [ ]:
import google_colab_selenium as gs
from bs4 import BeautifulSoup
import requests
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
import re
import pandas as pd
from lxml import etree
#import matplotlib.pyplot as plt
from selenium.webdriver.common.action_chains import ActionChains
import time
from selenium.webdriver.common.keys import Keys
import math
import pandas as pd
from selenium.webdriver.chrome.options import Options
from IPython.display import clear_output

In [ ]:
!pip install chromedriver-autoinstaller

import sys
sys.path.insert(0,'/usr/lib/chromium-browser/chromedriver')

import time
import pandas as pd
from bs4 import BeautifulSoup
from selenium import webdriver
import chromedriver_autoinstaller

# setup chrome options
chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument('--headless') # ensure GUI is off
chrome_options.add_argument('--no-sandbox')
chrome_options.add_argument('--disable-dev-shm-usage')
chrome_options.add_argument("--lang=ar")

# set path to chromedriver as per your configuration
chromedriver_autoinstaller.install()

# set the target URL
url = "put-url-here-to-scrape"

# set up the webdriver


# Methods

In [ ]:
def close_login_elemnt(driver):
    '''
    Closes the login popup element

    inputs:
        driver(webdriver) : The Web Driver will be used

    return:
        None
    '''
    elemnt=driver.find_element(By.CSS_SELECTOR,"[aria-label='Close']")
    elemnt.click()
def close_cookies_elemnt(driver):
    '''
    Closes the cookies popup element

    inputs:
        driver(webdriver) : The Web Driver will be used

    return:
        None
    '''
    element=driver.find_element(By.XPATH,"//*[@id='facebook']/body/div[3]/div[1]/div/div[2]/div/div/div/div/div[2]/div/div[2]/div[1]")
    element.click()

In [ ]:
def initlize_driver():
    opt=Options()
    opt.add_argument("--no-sandbox")
    opt.add_argument("--disable-dev-shm-usage")
    opt.add_argument("--lang=ar")
    driver = gs.Chrome(options=opt)
    return driver

def open_web_page(driver,url):
    '''
        Open A web page and close all popup elements

        inputs:
            driver(webdriver) : The Web Driver will be used
            url(str) : URL of Facebook page

        return:
            None
    '''
    try:
        driver.get(url) # Openning url
        try:
            #closing cookies elemnt if existed
            close_cookies_elemnt(driver)
        except:
            pass

        try:
            # closing login elemnt if existed
            close_login_elemnt(driver)
        except:
            pass
    except Exception as error:
        pass


In [ ]:
def scroll_page(driver,scrolls=10 ,sleep_time=5):

    '''
    Scrolls down throug the page

    inputs:
        driver(webdriver) : The Web Driver will be used
        scrolld(int) : Number of Scrolls after loading the page
        sleep_time(int): Number of seconds to wait between each scroll

    return:
        None

    '''

    scrolls= int(scrolls) # getting number of scrolls
    progress=0.1 # for printing progress of scrolling

    for i in range(scrolls):
        driver.execute_script("window.scrollTo(0, document.body.scrollHeight);") # executing Script that scroll the page

        if(float(i/scrolls)  >progress) and scrolls>9:
            print(f'progress: {int(progress *100)} %' , '  | number of scrolls= ' ,i) ## informing after each 10% of scrolling
            progress=progress+0.1
        time.sleep(int(sleep_time)) # waiting between each scroll to give time for posts to load
    print(f'progress: 100 %')

In [ ]:
def get_head_body(driver):
    '''
    inputs:
        driver(webdriver): The Web Driver will be used

    returns:
        head(etreeELement): Head Etree element
        body(etreeELement): Body Etree element
    '''
    # Getting Head Element
    head=driver.find_element(By.TAG_NAME,'head')
    headElemnt = head.get_attribute('outerHTML') #gives exact HTML content of the element
    headHtml = BeautifulSoup(headElemnt,'html') # Convert the string content into html elements
    headEtree= etree.HTML(str(headHtml)) # Convert the Element to etree elemnt (LXML)

    # Getting Body Elemnt
    body=driver.find_element(By.TAG_NAME,'body')
    bodyElemnt = body.get_attribute('outerHTML') #gives exact HTML content of the element
    bodyHtml = BeautifulSoup(bodyElemnt,'html') # Convert the string content into html elements
    bodyEtree = etree.HTML(str(bodyHtml)) # Convert the Element to etree elemnt (LXML)

    return headEtree , bodyEtree

In [ ]:
def get_posts_urls(driver):
    '''
    inputs:
        driver(webdriver): The Web Driver will be used

    returns:
        postsUrls(list): List of Posts URLs

    '''
    postsUrls=[]
    for i in range(500):
        added=False
        try:
            times=driver.find_element(By.XPATH,f'/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[1]/div/div/div[4]/div[2]/div/div[2]/div/div[{i+1}]/div/div/div/div/div/div/div/div/div/div/div[13]/div/div/div[4]/div/div/div[2]/div[3]/div[1]/div/div[2]/div[*]/ul/li/span/div/a')
            times=times.get_attribute('href')
            times=times.split('?')[0]
            postsUrls.append(times)
            added=True
        except:
            pass

        if not added:
            try:
                times=driver.find_element(By.XPATH,f'/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[1]/div/div/div[4]/div[2]/div/div[2]/div/div[{i+1}]/div/div/div/div/div/div/div/div/div/div/div[13]/div/div/div[4]/div/div/div[2]/div/div/div[2]/div[*]/ul/li/span/div/a')
                times=times.get_attribute('href')
                times=times.split('?')[0]
                postsUrls.append(times)
            except:
                pass

    return postsUrls

In [ ]:
def get_post_elements(driver,url):
    '''
     Get posts elemnts (comments, likes, contetn , creation_date & text)

    inputs:
        utl(str): URL of post page

    '''
    open_web_page(driver,url) # Open post page
    time.sleep(1)
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);") # executing Script that scroll the page
    head, body= get_head_body(driver) # Get Head & body HTML contents

    content='Other'

    if url.split('/')[4]=='videos':
        # Get text elemnt
        text=body.xpath('/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[2]/div[1]/div/div/div[2]/div[1]/div[3]/div/span')
        # Get likes elemnt
        likes=body.xpath('/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[2]/div[1]/div/div/div[1]/div[2]/div[2]/div/div/div[2]/div/div[1]/div/span/span/span')
        # Get comments elemnt
        comments=body.xpath('/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[2]/div[1]/div/div/div[1]/div[2]/div[2]/div/div/div[2]/div/div[3]/span/a/span/text()')
        # Get content element
        content= 'vid'

    else:
        # Get text elemnt
        text=body.xpath('/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[1]/div/div/div/div/div/div/div/div/div/div/div/div/div/div[13]/div/div/div[3]/div[1]/div/div/div/span')

        # Get likes elemnt
        likes=body.xpath('/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[1]/div/div/div/div/div/div/div/div/div/div/div/div/div/div[13]/div/div/div[4]/div/div/div[1]/div/div[1]/div/div[1]/span[2]/span/span')
        # Get content element
        content= body.xpath('/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[1]/div/div/div/div/div/div/div/div/div/div/div/div/div/div[13]/div/div/div[3]/div[2]/div[1]/a/div[1]/div/div/div/img')
        if content != None:
            content = 'img'

        try: # comments have some bugs, so some times they break the code
        # Get comments elemnt
            comments=body.xpath('/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[1]/div/div/div/div/div/div/div/div/div/div/div/div/div/div[13]/div/div/div[4]/div/div/div[1]/div/div[1]/div/div[2]/div[1]/span/a/div/div[1]/span')

            print(comments)
            comments=comments[0].text
        except:
            time.sleep(0.5)
            driver.execute_script("window.scrollTo(0, document.body.scrollHeight);") # executing Script that scroll the page
            head, body= get_head_body(driver) # Get Head & body HTML contents
            comments=body.xpath('/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[1]/div/div/div/div/div/div/div/div/div/div/div/div/div/div[13]/div/div/div[4]/div/div/div[1]/div/div[1]/div/div[2]/div[1]/span/a/div/div[1]/span')
            print(comments)
            comments=comments[0].text



    for line in text[0]:
        print(line.getchildren()[0].text)

    print('Likes: ' ,likes[0].text)
    print('comments: ' , comments)
    print('content: ' , content)


In [ ]:
def save_urls_to_csv(links,name):
  df = pd.DataFrame()
  df['id'] = range(1, len(links) + 1)
  df['link']=links
  df.to_csv(f'{name}_Links.csv', index=False)

# Main

In [ ]:
driver1 = webdriver.Chrome(options=chrome_options)

In [ ]:
driver1.get('https://www.facebook.com/login/')

#scroll_page(driver1,1,1)

In [ ]:
driver1.find_element(By.NAME, "email").send_keys('abdo.barca.boy@hotmail.com')
print ("Email Id entered")
time.sleep(1)

driver1.find_element(By.NAME, "pass").send_keys('modmengame222')
print ("Password entered")

driver1.find_element(By.NAME,"login").click()


Email Id entered
Password entered


In [ ]:
driver1.get('https://www.facebook.com/Mamdouh.NasrAllah/?locale=ar_AR')

In [ ]:
driver1.find_element(By.ID, ":R1oqqcqeaqkpaqH1:").send_keys('271576')

In [ ]:
element = driver1.find_elements(By.XPATH, "//a[contains(@href, 'https://www.facebook.com/AymanJadaofficial/posts')]")
len(element)

3

In [ ]:
element = driver1.find_elements(By.XPATH, "//a[contains(@href, 'https://www.facebook.com/AymanJadaofficial/videos')]")
len(element)

0

In [ ]:
df = pd.read_csv('/content/Awwad_links.csv',index_col=False)

In [ ]:
links = list()
links_set= set(links)



In [ ]:
len(links)

1962

In [ ]:
for i in range(200):
  clear_output()
  print('Iteration: ' , i ,' | size:', len(links))
  scroll_page(driver1,3,1)
  posts=driver1.find_elements(By.XPATH,"//a[starts-with(@href, 'https://www.facebook.com/Mamdouh.NasrAllah/posts')]")
  vids=driver1.find_elements(By.XPATH,"//a[starts-with(@href, 'https://www.facebook.com/Mamdouh.NasrAllah/videos')]")

  for i in posts:
    try:
      post_url=i.get_attribute('href')
      p=post_url.split('?')[0]
      if p not in links_set:
        links.append(p)
        links_set.add(p)
    except:
      pass
  for i in vids:
    try:
      vid_url=i.get_attribute('href')
      v=vid_url.split('?')[0]
      if v not in links_set:
        links.append(v)
        links_set.add(v)
    except:
      pass


Iteration:  199  | size: 2107
progress: 100 %


In [ ]:
save_urls_to_csv(links,'Mamdouh.NasrAllah')

In [ ]:


from google.colab import files

files.download('/content/Mamdouh.NasrAllah_Links.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
 driver1.get_screenshot_as_file('dd.png')

True

In [ ]:
driver1.find_element(By.XPATH,'/html/body/div[1]/div/div/div[1]/div/div[3]/div/div/div[1]/div[1]/div/div/div[4]/div[2]/div/div[2]/div[3]/div[1]/div/div/div/div/div/div/div/div/div/div/div[2]/div/div/div[2]/div/div[2]/div/div[2]/span/div/span[1]/span/a')

In [ ]:
driver1.page_source

'<html id="facebook" class="_9dls __fb-dark-mode _8ykn" lang="ar" dir="rtl"><head><link data-default-icon="https://static.xx.fbcdn.net/rsrc.php/yT/r/aGT3gskzWBf.ico" data-badged-icon="https://static.xx.fbcdn.net/rsrc.php/yD/r/UJj0tgk-RrT.ico" rel="shortcut icon" href="https://static.xx.fbcdn.net/rsrc.php/yT/r/aGT3gskzWBf.ico"><title>(1) Facebook</title><meta name="bingbot" content="noarchive"><meta name="viewport" content="width=device-width,initial-scale=1,maximum-scale=2,shrink-to-fit=no"><link rel="manifest" id="MANIFEST_LINK" href="/data/manifest/" crossorigin="use-credentials"><meta name="color-scheme" content="dark"><meta name="theme-color" content="#242526"><style nonce="">:root, .__fb-light-mode:root, .__fb-light-mode {--fds-black:#000000;--fds-black-alpha-05:rgba(0, 0, 0, 0.05);--fds-black-alpha-10:rgba(0, 0, 0, 0.1);--fds-black-alpha-15:rgba(0, 0, 0, 0.15);--fds-black-alpha-20:rgba(0, 0, 0, 0.2);--fds-black-alpha-30:rgba(0, 0, 0, 0.3);--fds-black-alpha-40:rgba(0, 0, 0, 0.4);-

In [ ]:
x=driver1.find_elements(By.CSS_SELECTOR,"[aria-label='Close']")
len(x)

1

In [ ]:
print(x[0].get_attribute('role'))
x[0].click()

button


In [ ]:
x=driver1.find_elements(By.XPATH,"//a[starts-with(@href, 'https://www.facebook.com/DhiabTarak/posts')]")
len(x)

1